Baltimore City

Requirements for Heating of Rental Units
(During the months of October 1st to April 30th)
• 70 degrees Fahrenheit in all habitable rooms, bath- rooms and toilet rooms with no room to be less than 65 degrees Fahrenheit during the hours of 5 a.m. to
midnight and
• 65 degrees Fahrenheit in all habitable rooms, bath-
rooms and toilet rooms with no room to be less than 60 degrees Fahrenheit during the hours of midnight to 5 a.m.


Baltimore County

(b) Heating facilities. (1) Except as provided in paragraph (2) of this subsection, during the period from October 15 to April 15, the property owner shall supply each housing unit with heat or heating equipment that is capable of supplying sufficient heat to maintain a room temperature of not less than: (i) 65 degrees Fahrenheit in all habitable areas during the hours between 6:30 a.m. and 11:30 p.m. of each day; and (ii) 60 degrees Fahrenheit during other hours. (2) When the exterior temperature falls below zero degrees Fahrenheit, a minimum room temperature of 60 degrees Fahrenheit shall be maintained or capable of being maintained at all times. (3) The temperature shall be measured at a point 3 feet above the floor and 3 feet from exterior walls.

In [8]:
now = time.time()
hour = int(time.strftime('%H', time.localtime(now)))
print(hour>20)

'''
import datetime
now = datetime.datetime.now()
print(now)
print(now.hour)
'''
print 1

False
1


In [3]:
## plot temperature and humidity on same plot

import time
import pandas as pd
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go

# initialize plotly to plot inside of Jupyter notebook
init_notebook_mode(connected=True)

import urllib2 # python 2
from StringIO import StringIO # python 2

# 1) either, read the data from a url (this will only work when on Hopkins network)
#url = 'http://192.168.1.7:5010/environmentlog'
#url = 'http://192.168.1.4:5010/environmentlog'
response = urllib2.urlopen(url)
html = response.read() # this is full text of the log file
html = StringIO(html)
df = pd.read_csv(html)

# 2) or, load a local copy of fridge.log into a pandas dataframe
#filePath = 'fridge.log'
#df = pd.read_csv(filePath)
#

# construct a plotly friendly date/time, format is 'yyyy-mm-dd HH:MM:SS'
# we will append a new column to df called 'DateTime'
def tmpFunc(now):
    return time.strftime('%Y-%m-%d %H:%M:%S', time.localtime(now))
                         
df['DateTime'] = df['Seconds'].apply(lambda x: tmpFunc(x))

# home, apply nightime (62f) and daytime (68f) 
'''
From 6 am to 10 pm: If the outside temperature falls below 55 degrees, the inside temperature must be at least 68 degrees everywhere in your apartment.
From 10 pm to 6 am: As of October 1, 2017, the inside temperature must be at least 62 degrees everywhere in your apartment regardless of the outside temperature.
'''
def tmpFunc2(now):
    hour = float(time.strftime('%H', time.localtime(now)))
    if hour >= 5 and hour<24:
        return 65 #70 #65 # 20 deg c
    else:
        return 60 #65 # 60 #16.6667 deg c
df['threshold'] = df['Seconds'].apply(lambda x: tmpFunc2(x))
mythreshold = df[['threshold']]
mythreshold2 = mythreshold.iloc[:]['threshold']

# home
# celcius to farenheight, (0°C × 9/5) + 32 = 32°F
def c2f(c):
    return (c * 9.0/5.0) + 32.0
df['farenheight'] = df['Temperature'].apply(lambda x: c2f(x))

df['color'] = ""
goodCount = 0.0
badCount = 0.0
for index, row in df.iterrows():
    #seconds = row['Seconds']
    #hour = int(int(time.strftime('%H', time.localtime(seconds))))
    if row['farenheight'] > row['threshold']:
        df.at[index,'color'] = 'rgb(17, 255, 17)' # green
        goodCount += 1
    else:
        df.at[index,'color'] = 'rgb(255, 17, 17)' # red
        badCount += 1
    # strip out bad readings
    if row['farenheight'] < 51:
            df.at[index,'farenheight'] = None
# % of reading that are good
print 'percent of time inside temperature is legal:', goodCount / (goodCount+badCount) * 100

farenheight = df[['farenheight']]
farenheight2 = farenheight.iloc[:]['farenheight']
# end home

# extact columns (these are not raw numbers yet)
myDateTime = df[['DateTime']]
myTemperature = df[['Temperature']]
myHumidity = df[['Humidity']]

# get the actual numbers from each column
myDateTime2 = myDateTime.iloc[:]['DateTime']
myTemperature2 = myTemperature.iloc[:]['Temperature'] * 100 # (0°C × 9/5) + 32 = 32°F
myHumidity2 = myHumidity.iloc[:]['Humidity']


# set up two traces to plot in plotly
trace1 = go.Scatter(
    x=myDateTime2,
    y=farenheight2,
    name='Temperature',
    mode='markers',
    marker= dict(size= 5,
                line= dict(width=1, color=df['color']),
                color= df['color'],
                opacity= 1
                )
)
trace2 = go.Scatter(
    x=myDateTime2,
    y=myHumidity2,
    name='Humidity',
    yaxis='y2'
)

# home
trace2 = go.Scatter(
    x=myDateTime2,
    y=mythreshold2,
    marker= dict(size= 5,
                line= dict(width=1, color='#000000'),
                color= '#000000',
                opacity= 1
                ),
    name='Threshold'
)

data = [trace1, trace2]

# make a plotly layout
layout = go.Layout(
    title='Temperature And Humidity',
    yaxis=dict(
        title='Temperature (deg fahrenheit)',
        titlefont=dict(
            # this is same as default plot color #1
            color='#1f77b4'
        ),
        tickfont=dict(
            # this is same as default plot color #1
            color='#1f77b4'
        )
    ),
    yaxis2=dict(
        title='Humidity (%)',
        #titlefont=dict(
        #    color='rgb(148, 103, 189)'
        #),
        #tickfont=dict(
        #    color='rgb(148, 103, 189)'
        #),
        titlefont=dict(
            # this is same as default plot color #2
            color='#ff7f0e'
        ),
        tickfont=dict(
            # this is same as default plot color #2
            color='#ff7f0e'
        ),
        overlaying='y',
        side='right'
    )
)

# plot with plotly
fig = go.Figure(data=data, layout=layout)
plot_url = iplot(fig, filename='multiple-axes-double')

percent of time inside temperature is legal: 38.2116977226


In [12]:
import Adafruit_IO
#from Adafruit_IO import Client
#from Adafruit_IO.errors import RequestError

aio = Adafruit_IO.Client('cudmore', '913a8573202c4854a34858cb5e334888')

#mqtt = Adafruit_IO.MQTTClient('cudmore', '913a8573202c4854a34858cb5e334888')

foo = aio.feeds('foo')
oldData = []
for f in farenheight2:
    #print(f)
    oldData.append(Adafruit_IO.Data(value=f))
    #aio.send_data(foo.key, f)

aio.send_batch_data(oldData)

# Send the value 100 to a feed called 'Foo'.
try:
    foo = aio.feeds('foo')
    aio.send_data(foo.key, 100)
except (Adafruit_IO.errors.RequestError) as e:
    print(str(e))

TypeError: send_batch_data() takes exactly 3 arguments (2 given)